### Cruzamento de dois conjuntos de dados públicos para deduzir a quantidade e os custos com os funcionários das Autarquias, Fundações e Empresas do Governo do Estado de São Paulo

Elaboração: Observatório do Ciclo de Planejamento e Gestão do Governo do Estado de São Paulo <br />
Data: 21-nov-2016 (v1), 13-jan-2017 (v2) <br />
Mais informações: http://aeppsp.org.br/observatorio-ciclo-planejamento-gestao/ <br />

Conjuntos de dados: <br />
A. Remuneração Mensal de Servidores e Empregados Públicos - Administração Direta e Indireta <br />
C. Relação de Funcionários - Administração Indireta <br />
Mais informações: http://aeppsp.org.br/observatorio-ciclo-planejamento-gestao/140-mapa-da-mina-recursos-humanos

#### Trata e consolida os arquivos do conjunto de dados 'C. Relação de Funcionários - Administração Indireta':

In [1]:
import pandas as pd
pd.set_option('display.max_rows', 5000)

In [2]:
def clean_df(df, nat_jur):
    df_tmp = df.copy()
    filtro = ((df_tmp.loc[:, 'UNIDADE DE TRABALHO'].isnull()) &
              (df_tmp.loc[:, 'ÓRGÃO - DESTINO DE AFASTAMENTO'].isnull()) &
              (df_tmp.loc[:, 'CARGO PERMANENTE'].isnull()) &
              (df_tmp.loc[:, 'AFASTADO P/ OUTROS ÓRGÃOS'].isnull()))
    df_tmp.loc[filtro, 'nome_orgao'] = df_tmp.loc[filtro, 'NOME']
    df_tmp.nome_orgao = df_tmp.nome_orgao.fillna(method='ffill')
    df_tmp = df_tmp.loc[~filtro]
    df_tmp = df_tmp.loc[~df_tmp['UNIDADE DE TRABALHO'].apply(lambda x: isinstance(x, int))]
    df_tmp['nat_juridica'] = nat_jur
    return df_tmp

In [3]:
df_autarquia = pd.read_excel('inputs/ConsultaEmpregados-Autarquias.xls', skiprows=1)
df_fundacao = pd.read_excel('inputs/ConsultaEmpregados-Fundacoes.xls', skiprows=1)
df_empresa = pd.read_excel('inputs/ConsultaEmpregados-Empresas.xls', skiprows=1)

df_autarquia_c = clean_df(df_autarquia, 'Autarquia')
df_fundacao_c = clean_df(df_fundacao, 'Fundação')
df_empresa_c = clean_df(df_empresa, 'Empresa')

In [4]:
df = pd.concat([df_autarquia_c, df_fundacao_c, df_empresa_c], ignore_index=True)

In [5]:
df.NOME = df.NOME.str.upper()

In [6]:
df.to_pickle('tmp/funcionarios_indireta.pickle')

In [7]:
df = pd.read_pickle('tmp/funcionarios_indireta.pickle')

In [8]:
len(df)

112587

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 112587 entries, 0 to 112586
Data columns (total 8 columns):
NOME                              112587 non-null object
CARGO PERMANENTE                  106808 non-null object
CARGO OU FUNÇÃO EM COMISSÃO       15346 non-null object
UNIDADE DE TRABALHO               112512 non-null object
AFASTADO P/ OUTROS ÓRGÃOS         112587 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO    1685 non-null object
nome_orgao                        112587 non-null object
nat_juridica                      112587 non-null object
dtypes: object(8)
memory usage: 6.9+ MB


In [10]:
df.head(2)

NOME CARGO PERMANENTE CARGO OU FUNÇÃO EM COMISSÃO  \
0      AUGUSTO MUNIZ CAMPOS              NaN   ASSISTENTE DE GABINETE I    
1  CAROLINA DE SOUZA PRIETO              NaN      ASSISTENTE TÉCNICO III   

                              UNIDADE DE TRABALHO AFASTADO P/ OUTROS ÓRGÃOS  \
0  AGEM-AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA                       NÃO   
1  AGEM-AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA                       NÃO   

  ÓRGÃO - DESTINO DE AFASTAMENTO  \
0                            NaN   
1                            NaN   

                                         nome_orgao nat_juridica  
0  AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA    Autarquia  
1  AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA    Autarquia

#### Cria arquivo tratado e consolidado a partir do conjunto de dados 'C. Relação de Funcionários - Administração Indireta':

In [11]:
df.to_csv('outputs/Quadro-Funcionarios-Autarquias-Fundacoes-Empresas.csv')

#### Número de funcionários por tipo (comissionados puros, comissionados efetivos (híbridos), efetivos) nas Autarquias, Fundações e Empresas por Natureza Jurídica:

In [12]:
len(df)

112587

In [13]:
df.nat_juridica.value_counts()

Autarquia    52074
Empresa      41258
Fundação     19255
Name: nat_juridica, dtype: int64

In [14]:
df_comissionados_autarquias = df[(df.nat_juridica == 'Autarquia') &
                                 (~df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                                 (df['CARGO PERMANENTE'].isnull())]
len(df_comissionados_autarquias)

3108

In [15]:
df_comissionados_fundacoes = df[(df.nat_juridica == 'Fundação') &
                                (~df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                                (df['CARGO PERMANENTE'].isnull())]
len(df_comissionados_fundacoes)

639

In [16]:
df_comissionados_empresas = df[(df.nat_juridica == 'Empresa') &
                               (~df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                               (df['CARGO PERMANENTE'].isnull())]
len(df_comissionados_empresas)

2030

In [17]:
df_hibridos_autarquias = df[(df.nat_juridica == 'Autarquia') &
                            (~df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                            (~df['CARGO PERMANENTE'].isnull())]
len(df_hibridos_autarquias)

4214

In [18]:
df_hibridos_fundacoes = df[(df.nat_juridica == 'Fundação') &
                           (~df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                           (~df['CARGO PERMANENTE'].isnull())]
len(df_hibridos_fundacoes)

2196

In [19]:
df_hibridos_empresas = df[(df.nat_juridica == 'Empresa') &
                          (~df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                          (~df['CARGO PERMANENTE'].isnull())]
len(df_hibridos_empresas)

3159

In [20]:
df_efetivos_autarquias = df[(df.nat_juridica == 'Autarquia') &
                            (df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                            (~df['CARGO PERMANENTE'].isnull())]
len(df_efetivos_autarquias)

44750

In [21]:
df_efetivos_fundacoes = df[(df.nat_juridica == 'Fundação') &
                           (df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                           (~df['CARGO PERMANENTE'].isnull())]
len(df_efetivos_fundacoes)

16420

In [22]:
df_efetivos_empresas = df[(df.nat_juridica == 'Empresa') &
                          (df['CARGO OU FUNÇÃO EM COMISSÃO'].isnull()) &
                          (~df['CARGO PERMANENTE'].isnull())]
len(df_efetivos_empresas)

36069

#### Número de funcionários nas Autarquias, Fundações e Empresas [formalmente] afastados para outros órgãos:

In [23]:
df['AFASTADO P/ OUTROS ÓRGÃOS'].value_counts().to_frame()

AFASTADO P/ OUTROS ÓRGÃOS
NÃO                     110877
SIM                       1710

#### Número de funcionários nas Autarquias, Fundações e Empresas por Órgão:

In [24]:
len(df['nome_orgao']) # Número de funcionários

112587

In [25]:
len(df['nome_orgao'].value_counts()) # Número de órgãos

62

In [26]:
df['nome_orgao'].value_counts()

CEETEPS - CENTRO DE EDUCAÇÃO TECNOLÓGICA PAULA SOUZA                                                    19611
SABESP - COMPANHIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO                                          14279
FUNDAÇÃO CASA - FUNDAÇÃO CENTRO DE ATENDIMENTO SOCIOEDUCATIVO AO ADOLESCENTE                            12839
HCFMUSP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DA USP                                         11181
METRÔ - COMPANHIA DO METROPOLITANO DE SÃO PAULO                                                          9289
CPTM - COMPANHIA PAULISTA DE TRENS METROPOLITANOS                                                        8166
IAMSPE - INSTITUTO DE ASSISTÊNCIA MÉDICA AO SERVIDOR PÚBLICO                                             5110
HCFMRP-USP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DE RIBEIRÃO PRETO-USP                        4966
DER - DEPARTAMENTO DE ESTRADAS DE RODAGEM                                                                3138
CETESB - C

#### Número de 'comissionados puros' nas Autarquias, Fundações e Empresas por Órgão:

In [27]:
df_tmp = df_comissionados_autarquias['nome_orgao'].value_counts()
df_tmp[~df_tmp.isnull()].sort_values(ascending=False)

CEETEPS - CENTRO DE EDUCAÇÃO TECNOLÓGICA PAULA SOUZA                                                   905
HCFMUSP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DA USP                                        848
DETRAN - DEPARTAMENTO ESTADUAL DE TRÂNSITO                                                             412
DER - DEPARTAMENTO DE ESTRADAS DE RODAGEM                                                              247
JUCESP - JUNTA COMERCIAL DO ESTADO DE SÃO PAULO                                                        180
IPEM-SP - INSTITUTO DE PESOS E MEDIDAS DO ESTADO DE SÃO PAULO                                           84
HCFMB - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DE BOTUCATU                                      84
SPPREV - SÃO PAULO PREVIDÊNCIA                                                                          71
DAESP - DEPARTAMENTO AEROVIÁRIO DO ESTADO DE SÃO PAULO                                                  60
ARTESP - AGÊNCIA REGULADORA DE TRANSP

In [28]:
df_tmp = df_comissionados_fundacoes['nome_orgao'].value_counts()
df_tmp[~df_tmp.isnull()].sort_values(ascending=False)

FUNDAÇÃO PADRE ANCHIETA - RÁDIO E TV EDUCATIVAS                                                         169
FUNDAÇÃO PARA A CONSERVAÇÃO E A PRODUÇÃO FLORESTAL                                                      104
SP-PREVCOM - FUNDAÇÃO DE PREVIDÊNCIA COMPLEMENTAR DO ESTADO DE SÃO PAULO                                 70
FAPESP - FUNDAÇÃO DE AMPARO À PESQUISA DO ESTADO DE SÃO PAULO                                            49
FUNAP - FUNDAÇÃO "PROF. DR.  MANOEL PEDRO PIMENTEL" DE AMPARO AO PRESO                                   47
FUNDAÇÃO MEMORIAL DA AMÉRICA LATINA                                                                      33
FUNDAÇÃO PRÓ-SANGUE HEMOCENTRO DE SÃO PAULO                                                              26
PROCON-SP - FUNDAÇÃO DE PROTEÇÃO E DEFESA DO CONSUMIDOR                                                  26
FURP - FUNDAÇÃO PARA O REMÉDIO POPULAR “CHOPIN TAVARES LIMA”                                             25
FUNDAÇÃO ONCOCENTRO DE SÃO P

In [29]:
df_tmp = df_comissionados_empresas['nome_orgao'].value_counts()
df_tmp[~df_tmp.isnull()].sort_values(ascending=False)

METRÔ - COMPANHIA DO METROPOLITANO DE SÃO PAULO                               741
PRODESP - COMPANHIA DE PROCESSAMENTO DE DADOS DO ESTADO DE SÃO PAULO          344
IMESP - IMPRENSA OFICIAL DO ESTADO S.A.                                       186
DERSA - DESENVOLVIMENTO RODOVIÁRIO S.A.                                       173
EMTU – EMPRESA METROPOLITANA DE TRANSPORTES URBANOS                           124
CPOS - COMPANHIA PAULISTA DE OBRAS E SERVIÇOS                                 105
CETESB - COMPANHIA AMBIENTAL DO ESTADO DE SÃO PAULO                            56
SABESP - COMPANHIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO                 52
CESP - COMPANHIA ENERGÉTICA DE SÃO PAULO                                       47
IPT - INSTITUTO DE PESQUISAS TECNOLÓGICAS                                      41
EMPLASA - EMPRESA PAULISTA DE PLANEJAMENTO METROPOLITANO SA                    40
CDHU - COMPANHIA DE DESENVOLVIMENTO HABITACIONAL E URBANO                      35
COMPANHIA PAULIS

#### Taxa de 'comissionados puros' sobre o total de funcionários por Órgão:

In [30]:
df_tmp = df_comissionados_autarquias['nome_orgao'].value_counts() / df['nome_orgao'].value_counts()
df_tmp[~df_tmp.isnull()].sort_values(ascending=False) * 100

AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA                                                       100.000000
ARTESP - AGÊNCIA REGULADORA DE TRANSPORTES                                                             100.000000
AGEMCAMP - AGÊNCIA METROPOLITANA DE CAMPINAS                                                           100.000000
IPESP - INSTITUTO DE PAGAMENTOS ESPECIAIS DE SÃO PAULO                                                 100.000000
JUCESP - JUNTA COMERCIAL DO ESTADO DE SÃO PAULO                                                         99.447514
SUTACO-SUP. TRAB. ARTESANAL COMUNIDADES - *EXTINTA PELA LEI Nº 15.828/2015 E DECRETO Nº 61.774/2015     45.833333
DAESP - DEPARTAMENTO AEROVIÁRIO DO ESTADO DE SÃO PAULO                                                  35.294118
DETRAN - DEPARTAMENTO ESTADUAL DE TRÂNSITO                                                              26.822917
SPPREV - SÃO PAULO PREVIDÊNCIA                                                          

In [31]:
df_tmp = df_comissionados_fundacoes['nome_orgao'].value_counts() / df['nome_orgao'].value_counts()
df_tmp[~df_tmp.isnull()].sort_values(ascending=False) * 100

SP-PREVCOM - FUNDAÇÃO DE PREVIDÊNCIA COMPLEMENTAR DO ESTADO DE SÃO PAULO                                100.000000
FUNDAÇÃO MEMORIAL DA AMÉRICA LATINA                                                                      50.000000
UNIVESP - FUNDAÇÃO UNIVERSIDADE VIRTUAL DO ESTADO DE SÃO PAULO                                           37.209302
FUNDAÇÃO ONCOCENTRO DE SÃO PAULO                                                                         25.274725
FUNDAÇÃO PARA A CONSERVAÇÃO E A PRODUÇÃO FLORESTAL                                                       24.880383
FUNDAÇÃO PADRE ANCHIETA - RÁDIO E TV EDUCATIVAS                                                          22.062663
FAPESP - FUNDAÇÃO DE AMPARO À PESQUISA DO ESTADO DE SÃO PAULO                                            16.780822
FUNAP - FUNDAÇÃO "PROF. DR.  MANOEL PEDRO PIMENTEL" DE AMPARO AO PRESO                                   13.091922
CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA - *EXTINTA PELA LEI Nº 15.899/2015 E DECRET

In [32]:
df_tmp = df_comissionados_empresas['nome_orgao'].value_counts() / df['nome_orgao'].value_counts()
df_tmp[~df_tmp.isnull()].sort_values(ascending=False) * 100

CPP - COMPANHIA PAULISTA DE PARCERIAS                                         100.000000
COMPANHIA PAULISTA DE EVENTOS E TURISMO - *EXTINTA PELA LEI Nº 15.827/2015    100.000000
COMPANHIA PAULISTA DE SECURITIZAÇÃO                                           100.000000
CPOS - COMPANHIA PAULISTA DE OBRAS E SERVIÇOS                                  38.181818
DERSA - DESENVOLVIMENTO RODOVIÁRIO S.A.                                        33.723197
IMESP - IMPRENSA OFICIAL DO ESTADO S.A.                                        23.664122
EMTU – EMPRESA METROPOLITANA DE TRANSPORTES URBANOS                            23.664122
EMPLASA - EMPRESA PAULISTA DE PLANEJAMENTO METROPOLITANO SA                    23.121387
COSESP - COMPANHIA DE SEGUROS DO ESTADO DE SÃO PAULO                           22.500000
PRODESP - COMPANHIA DE PROCESSAMENTO DE DADOS DO ESTADO DE SÃO PAULO           17.731959
COMPANHIA DOCAS DE SÃO SEBASTIÃO                                               13.592233
METRÔ - COMPANHIA DO 

#### Cruza os arquivos do conjunto de dados 'A. Remuneração Mensal de Servidores e Empregados Públicos - Administração Direta e Indireta' com o conjunto de dados 'C. Relação de Funcionários - Administração Indireta':

In [33]:
df_renda = pd.read_csv('inputs/Remuneracao.zip', compression='zip',
                       encoding='windows-1252', delimiter=';', decimal=',')

In [34]:
df_renda.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1096997 entries, 0 to 1096996
Data columns (total 10 columns):
NOME                                       1096997 non-null object
CARGO                                      1096978 non-null object
CARGO.1                                    1096997 non-null object
REMUNERAÇÃO DO MÊS                         1096997 non-null float64
FÉRIAS E 13º SALÁRIO                       1096997 non-null float64
PAGAMENTOS EVENTUAIS                       1096997 non-null float64
LICENÇA PRÊMIO INDENIZADA                  1096997 non-null float64
ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES    1096997 non-null float64
REDUTOR SALARIAL                           1096997 non-null float64
TOTAL LIQUÍDO (R$)                         1096997 non-null float64
dtypes: float64(7), object(3)
memory usage: 83.7+ MB


In [35]:
df_merge_autarquias = pd.merge(df_comissionados_autarquias, df_renda, how='left', left_on='NOME', right_on='NOME')

In [36]:
df_merge_fundacoes = pd.merge(df_comissionados_fundacoes, df_renda, how='left', left_on='NOME', right_on='NOME')

In [37]:
df_merge_empresas = pd.merge(df_comissionados_empresas, df_renda, how='left', left_on='NOME', right_on='NOME')

In [38]:
len(df_comissionados_autarquias)

3108

In [39]:
len(df_comissionados_fundacoes)

639

In [40]:
len(df_comissionados_empresas)

2030

In [41]:
len(df_renda)

1096997

In [42]:
len(df_merge_autarquias)

5264

In [43]:
len(df_merge_fundacoes)

902

In [44]:
len(df_merge_empresas)

3202

In [45]:
len(df_merge_autarquias) - len(df_comissionados_autarquias)

2156

In [46]:
len(df_merge_fundacoes) - len(df_comissionados_fundacoes)

263

In [47]:
len(df_merge_empresas) - len(df_comissionados_empresas)

1172

In [48]:
df_merge_autarquias.head(2)

NOME CARGO PERMANENTE CARGO OU FUNÇÃO EM COMISSÃO  \
0      AUGUSTO MUNIZ CAMPOS              NaN   ASSISTENTE DE GABINETE I    
1  CAROLINA DE SOUZA PRIETO              NaN      ASSISTENTE TÉCNICO III   

                              UNIDADE DE TRABALHO AFASTADO P/ OUTROS ÓRGÃOS  \
0  AGEM-AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA                       NÃO   
1  AGEM-AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA                       NÃO   

  ÓRGÃO - DESTINO DE AFASTAMENTO  \
0                            NaN   
1                            NaN   

                                         nome_orgao nat_juridica  \
0  AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA    Autarquia   
1  AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA    Autarquia   

                    CARGO CARGO.1  REMUNERAÇÃO DO MÊS  FÉRIAS E 13º SALÁRIO  \
0                     NaN     NaN                 NaN                   NaN   
1  ASSISTENTE TECNICO III    AGEM             3702.82                   0.0   

   PAGAMENTOS EVENTUAIS  LICENÇA PRÊMIO INDENIZADA  \
0                   NaN                        NaN   
1                   0.0                        0.0   

   ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES  REDUTOR SALARIAL  \
0                                      NaN               NaN   
1                                      0.0               0.0   

   TOTAL LIQUÍDO (R$)  
0                 NaN  
1             2161.79

In [49]:
df_merge_fundacoes.head(2)

NOME CARGO PERMANENTE CARGO OU FUNÇÃO EM COMISSÃO  \
0  ALEXANDRE DE OLIVEIRA              NaN          CHEFE DE SERVIÇO 1   
1  ALEXANDRE DE OLIVEIRA              NaN          CHEFE DE SERVIÇO 1   

                    UNIDADE DE TRABALHO AFASTADO P/ OUTROS ÓRGÃOS  \
0  CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA                       NÃO   
1  CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA                       NÃO   

  ÓRGÃO - DESTINO DE AFASTAMENTO  \
0                            NaN   
1                            NaN   

                                          nome_orgao nat_juridica  \
0  CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA - *EXTINT...     Fundação   
1  CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA - *EXTINT...     Fundação   

                          CARGO   CARGO.1  REMUNERAÇÃO DO MÊS  \
0  PROFESSOR EDUCACAO BASICA II  EDUCACAO             3439.45   
1                      2SGT  PM    SPPREV             5768.31   

   FÉRIAS E 13º SALÁRIO  PAGAMENTOS EVENTUAIS  LICENÇA PRÊMIO INDENIZADA  \
0                   0.0               -329.92                        0.0   
1                   0.0                  0.00                        0.0   

   ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES  REDUTOR SALARIAL  \
0                                   166.76               0.0   
1                                     0.00               0.0   

   TOTAL LIQUÍDO (R$)  
0             2852.81  
1             3211.50

In [50]:
df_merge_empresas.head(2)

NOME CARGO PERMANENTE  \
0            ADAO BORGES VASCONCELOS              NaN   
1  ANTONIO CARLOS DE OLIVEIRA JUNIOR              NaN   

  CARGO OU FUNÇÃO EM COMISSÃO                  UNIDADE DE TRABALHO  \
0          ASSESSOR EXECUTIVO  DIRETORIA ADMINISTRATIVA FINANCEIRA   
1          ASSESSOR EXECUTIVO    NUCLEO REGIONAL DE RIBEIRAO PRETO   

  AFASTADO P/ OUTROS ÓRGÃOS ÓRGÃO - DESTINO DE AFASTAMENTO  \
0                       NÃO                            NaN   
1                       NÃO                            NaN   

                                          nome_orgao nat_juridica  \
0  CDHU - COMPANHIA DE DESENVOLVIMENTO HABITACION...      Empresa   
1  CDHU - COMPANHIA DE DESENVOLVIMENTO HABITACION...      Empresa   

                CARGO CARGO.1  REMUNERAÇÃO DO MÊS  FÉRIAS E 13º SALÁRIO  \
0  ASSESSOR EXECUTIVO    CDHU             18036.2                   0.0   
1                 NaN     NaN                 NaN                   NaN   

   PAGAMENTOS EVENTUAIS  LICENÇA PRÊMIO INDENIZADA  \
0                   0.0                        0.0   
1                   NaN                        NaN   

   ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES  REDUTOR SALARIAL  \
0                                 59583.89               0.0   
1                                      NaN               NaN   

   TOTAL LIQUÍDO (R$)  
0            51523.37  
1                 NaN

#### Nomes dos órgãos no conjunto de dados 'C':

In [51]:
set(df_comissionados_autarquias.nome_orgao)

{'AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA',
 'AGEMCAMP - AGÊNCIA METROPOLITANA DE CAMPINAS',
 'ARSESP - AGÊNCIA REGULADORA DE SANEAMENTO E ENERGIA',
 'ARTESP - AGÊNCIA REGULADORA DE TRANSPORTES',
 'CAIXA BENEFICENTE DA POLÍCIA MILITAR',
 'CEETEPS - CENTRO DE EDUCAÇÃO TECNOLÓGICA PAULA SOUZA',
 'DAEE - DEPARTAMENTO DE ÁGUAS E ENERGIA ELÉTRICA',
 'DAESP - DEPARTAMENTO AEROVIÁRIO DO ESTADO DE SÃO PAULO',
 'DER - DEPARTAMENTO DE ESTRADAS DE RODAGEM',
 'DETRAN - DEPARTAMENTO ESTADUAL DE TRÂNSITO',
 'FAMEMA - FACULDADE DE MEDICINA DE MARÍLIA',
 'FAMERP - FACULDADE DE MEDICINA DE SÃO JOSÉ DO RIO PRETO',
 'HCFMB - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DE BOTUCATU',
 'HCFMRP-USP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DE RIBEIRÃO PRETO-USP',
 'HCFMUSP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DA USP',
 'IAMSPE - INSTITUTO DE ASSISTÊNCIA MÉDICA AO SERVIDOR PÚBLICO',
 'IMESC - INSTITUTO DE MEDICINA SOCIAL E DE CRIMINOLOGIA',
 'IPEM-SP - INSTITUTO DE PESOS E MEDID

In [52]:
set(df_comissionados_fundacoes.nome_orgao)

{'CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA - *EXTINTA PELA LEI Nº 15.899/2015 E DECRETO Nº 61.964/2016',
 'FAPESP - FUNDAÇÃO DE AMPARO À PESQUISA DO ESTADO DE SÃO PAULO',
 'FDE - FUNDAÇÃO PARA O DESENVOLVIMENTO DA EDUCAÇÃO',
 'FUNAP - FUNDAÇÃO "PROF. DR.  MANOEL PEDRO PIMENTEL" DE AMPARO AO PRESO',
 'FUNDAP - FUNDAÇÃO DO DESENVOLVIMENTO ADMINISTRATIVO - *EXTINÇÃO REGULAMENTADA PELO DECRETO Nº 61.866',
 'FUNDAÇÃO MEMORIAL DA AMÉRICA LATINA',
 'FUNDAÇÃO ONCOCENTRO DE SÃO PAULO',
 'FUNDAÇÃO PADRE ANCHIETA - RÁDIO E TV EDUCATIVAS',
 'FUNDAÇÃO PARA A CONSERVAÇÃO E A PRODUÇÃO FLORESTAL',
 'FUNDAÇÃO PARQUE ZOOLÓGICO DE SÃO PAULO',
 'FUNDAÇÃO PRÓ-SANGUE HEMOCENTRO DE SÃO PAULO',
 'FURP - FUNDAÇÃO PARA O REMÉDIO POPULAR “CHOPIN TAVARES LIMA”',
 'ITESP - FUNDAÇÃO INSTITUTO DE TERRAS DO ESTADO DE SÃO PAULO "JOSÉ GOMES DA SILVA"',
 'PROCON-SP - FUNDAÇÃO DE PROTEÇÃO E DEFESA DO CONSUMIDOR',
 'SP-PREVCOM - FUNDAÇÃO DE PREVIDÊNCIA COMPLEMENTAR DO ESTADO DE SÃO PAULO',
 'UNIVESP - FUNDAÇÃO UNIVERSIDADE VI

In [53]:
set(df_comissionados_empresas.nome_orgao)

{'CDHU - COMPANHIA DE DESENVOLVIMENTO HABITACIONAL E URBANO',
 'CESP - COMPANHIA ENERGÉTICA DE SÃO PAULO',
 'CETESB - COMPANHIA AMBIENTAL DO ESTADO DE SÃO PAULO',
 'COMPANHIA DOCAS DE SÃO SEBASTIÃO',
 'COMPANHIA PAULISTA DE EVENTOS E TURISMO - *EXTINTA PELA LEI Nº 15.827/2015',
 'COMPANHIA PAULISTA DE SECURITIZAÇÃO',
 'COSESP - COMPANHIA DE SEGUROS DO ESTADO DE SÃO PAULO',
 'CPOS - COMPANHIA PAULISTA DE OBRAS E SERVIÇOS',
 'CPP - COMPANHIA PAULISTA DE PARCERIAS',
 'DERSA - DESENVOLVIMENTO RODOVIÁRIO S.A.',
 'EMAE - EMPRESA METROPOLITANA DE ÁGUAS E ENERGIA',
 'EMPLASA - EMPRESA PAULISTA DE PLANEJAMENTO METROPOLITANO SA',
 'EMTU – EMPRESA METROPOLITANA DE TRANSPORTES URBANOS',
 'IMESP - IMPRENSA OFICIAL DO ESTADO S.A.',
 'IPT - INSTITUTO DE PESQUISAS TECNOLÓGICAS',
 'METRÔ - COMPANHIA DO METROPOLITANO DE SÃO PAULO',
 'PRODESP - COMPANHIA DE PROCESSAMENTO DE DADOS DO ESTADO DE SÃO PAULO',
 'SABESP - COMPANHIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO'}

#### Nomes dos órgãos no conjunto de dados 'A':

In [54]:
set(df_renda['CARGO.1'])

{'ADM GERAL',
 'AGEM',
 'AGEMCAMP',
 'AGEMVALE',
 'ARSESP',
 'ARTESP',
 'CASA CIVIL',
 'CBPM',
 'CDHU',
 'CEETEPS',
 'CESP',
 'CETESB',
 'CIA DOCAS',
 'CODASP',
 'COSESP',
 'CPOS',
 'CPP',
 'CPSEC',
 'CPTM',
 'CULTURA',
 'DAEE',
 'DAESP',
 'DER',
 'DERSA',
 'DESENVOLVE SP',
 'DETRAN',
 'EDUCACAO',
 'EMAE',
 'EMPLASA',
 'EMTU',
 'ENERGIA',
 'ESPORTE',
 'FAMEMA',
 'FAPESP',
 'FAZENDA',
 'FDE',
 'FMSJRPRETO',
 'FOSP',
 'FUNAP',
 'FUND. CASA',
 'FUND. FLORESTAL',
 'FURP',
 'GAB GOV',
 'GESTAO PUBLICA',
 'HABITACAO',
 'HCFMB',
 'HCFMRP',
 'HCFMUSP',
 'IMESC',
 'IMESP',
 'INSTITUTO DE ASSISTENCIA MEDICA SERVIDOR',
 'IPEM',
 'IPESP',
 'IPT',
 'ITESP',
 'JUCESP',
 'JUSTICA',
 'MEIO AMBIENTE',
 'MEMORIAL',
 'METRO',
 'PE. ANCHIETA',
 'PGE',
 'PM',
 'PRO-SANGUE',
 'PROCON',
 'PRODESP',
 'RECURSOS HIDRICOS',
 'SAA',
 'SABESP',
 'SAP',
 'SAUDE',
 'SDECTI',
 'SDPD',
 'SDS',
 'SEADE',
 'SECRETARIA DE GOVERNO',
 'SEPLAN',
 'SERT',
 'SP.CLIN.FAC.MED.MARILIA-HCFAMEMA',
 'SPPREV',
 'SPPREVCOM',
 'SSP',


#### Dicionário para conectar os nomes dos órgãos nos dois conjuntos de dados:

In [55]:
dicionario_orgaos = {'CDHU - COMPANHIA DE DESENVOLVIMENTO HABITACIONAL E URBANO': 'CDHU',
 'CEPAM - FUNDAÇÃO PREFEITO FARIA LIMA - *EXTINTA PELA LEI Nº 15.899/2015 E DECRETO Nº 61.964/2016': 'SEPLAN',
 'CESP - COMPANHIA ENERGÉTICA DE SÃO PAULO': 'CESP',
 'CETESB - COMPANHIA AMBIENTAL DO ESTADO DE SÃO PAULO': 'CETESB',
 'COMPANHIA DOCAS DE SÃO SEBASTIÃO': 'CIA DOCAS',
 'COMPANHIA PAULISTA DE EVENTOS E TURISMO - *EXTINTA PELA LEI Nº 15.827/2015': '####',
 'COMPANHIA PAULISTA DE SECURITIZAÇÃO': 'CPSEC',
 'COSESP - COMPANHIA DE SEGUROS DO ESTADO DE SÃO PAULO': 'COSESP',
 'CPOS - COMPANHIA PAULISTA DE OBRAS E SERVIÇOS': 'CPOS',
 'CPP - COMPANHIA PAULISTA DE PARCERIAS': 'CPP',
 'DERSA - DESENVOLVIMENTO RODOVIÁRIO S.A.': 'DERSA',
 'EMAE - EMPRESA METROPOLITANA DE ÁGUAS E ENERGIA': 'EMAE',
 'EMPLASA - EMPRESA PAULISTA DE PLANEJAMENTO METROPOLITANO SA': 'EMPLASA',
 'EMTU – EMPRESA METROPOLITANA DE TRANSPORTES URBANOS': 'EMTU',
 'FAPESP - FUNDAÇÃO DE AMPARO À PESQUISA DO ESTADO DE SÃO PAULO': 'FAPESP',
 'FDE - FUNDAÇÃO PARA O DESENVOLVIMENTO DA EDUCAÇÃO': 'FDE',
 'FUNAP - FUNDAÇÃO "PROF. DR.  MANOEL PEDRO PIMENTEL" DE AMPARO AO PRESO': 'FUNAP',
 'FUNDAP - FUNDAÇÃO DO DESENVOLVIMENTO ADMINISTRATIVO - *EXTINÇÃO REGULAMENTADA PELO DECRETO Nº 61.866': 'SEPLAN',
 'FUNDAÇÃO MEMORIAL DA AMÉRICA LATINA': 'MEMORIAL',
 'FUNDAÇÃO ONCOCENTRO DE SÃO PAULO': 'FOSP',
 'FUNDAÇÃO PADRE ANCHIETA - RÁDIO E TV EDUCATIVAS': 'PE. ANCHIETA',
 'FUNDAÇÃO PARA A CONSERVAÇÃO E A PRODUÇÃO FLORESTAL': 'FUND. FLORESTAL',
 'FUNDAÇÃO PARQUE ZOOLÓGICO DE SÃO PAULO': 'ZOOLOGICO',
 'FUNDAÇÃO PRÓ-SANGUE HEMOCENTRO DE SÃO PAULO': 'PRO-SANGUE',
 'FURP - FUNDAÇÃO PARA O REMÉDIO POPULAR “CHOPIN TAVARES LIMA”': 'FURP',
 'IMESP - IMPRENSA OFICIAL DO ESTADO S.A.': 'IMESP',
 'IPT - INSTITUTO DE PESQUISAS TECNOLÓGICAS': 'IPT',
 'ITESP - FUNDAÇÃO INSTITUTO DE TERRAS DO ESTADO DE SÃO PAULO "JOSÉ GOMES DA SILVA"': 'ITESP',
 'METRÔ - COMPANHIA DO METROPOLITANO DE SÃO PAULO': 'METRO',
 'PROCON-SP - FUNDAÇÃO DE PROTEÇÃO E DEFESA DO CONSUMIDOR': 'PROCON',
 'PRODESP - COMPANHIA DE PROCESSAMENTO DE DADOS DO ESTADO DE SÃO PAULO': 'PRODESP',
 'SABESP - COMPANHIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO': 'SABESP',
 'SP-PREVCOM - FUNDAÇÃO DE PREVIDÊNCIA COMPLEMENTAR DO ESTADO DE SÃO PAULO': 'SPPREVCOM',
 'UNIVESP - FUNDAÇÃO UNIVERSIDADE VIRTUAL DO ESTADO DE SÃO PAULO': 'UNIVESP',
 'AGEM - AGÊNCIA METROPOLITANA DA BAIXADA SANTISTA': 'AGEM',
 'AGEMCAMP - AGÊNCIA METROPOLITANA DE CAMPINAS': 'AGEMCAMP',
 'ARSESP - AGÊNCIA REGULADORA DE SANEAMENTO E ENERGIA': 'ARSESP',
 'ARTESP - AGÊNCIA REGULADORA DE TRANSPORTES': 'ARTESP',
 'CAIXA BENEFICENTE DA POLÍCIA MILITAR': 'CBPM',
 'CEETEPS - CENTRO DE EDUCAÇÃO TECNOLÓGICA PAULA SOUZA': 'CEETEPS',
 'DAEE - DEPARTAMENTO DE ÁGUAS E ENERGIA ELÉTRICA': 'DAEE',
 'DAESP - DEPARTAMENTO AEROVIÁRIO DO ESTADO DE SÃO PAULO': 'DAESP',
 'DER - DEPARTAMENTO DE ESTRADAS DE RODAGEM': 'DER',
 'DETRAN - DEPARTAMENTO ESTADUAL DE TRÂNSITO': 'DETRAN',
 'FAMEMA - FACULDADE DE MEDICINA DE MARÍLIA': 'FAMEMA',
 'FAMEMA - FACULDADE DE MEDICINA DE MARÍLIA': 'SP.CLIN.FAC.MED.MARILIA-HCFAMEMA',
 'FAMERP - FACULDADE DE MEDICINA DE SÃO JOSÉ DO RIO PRETO': 'FMSJRPRETO',
 'HCFMB - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DE BOTUCATU': 'HCFMB',
 'HCFMRP-USP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DE RIBEIRÃO PRETO-USP': 'HCFMRP',
 'HCFMUSP - HOSPITAL DAS CLÍNICAS DA FACULDADE DE MEDICINA DA USP': 'HCFMUSP',
 'IAMSPE - INSTITUTO DE ASSISTÊNCIA MÉDICA AO SERVIDOR PÚBLICO': 'INSTITUTO DE ASSISTENCIA MEDICA SERVIDOR',
 'IMESC - INSTITUTO DE MEDICINA SOCIAL E DE CRIMINOLOGIA': 'IMESC',
 'IPEM-SP - INSTITUTO DE PESOS E MEDIDAS DO ESTADO DE SÃO PAULO': 'IPEM',
 'IPESP - INSTITUTO DE PAGAMENTOS ESPECIAIS DE SÃO PAULO': 'IPESP',
 'JUCESP - JUNTA COMERCIAL DO ESTADO DE SÃO PAULO': 'JUCESP',
 'SPPREV - SÃO PAULO PREVIDÊNCIA': 'SPPREV',
 'SUCEN - SUPERINTENDÊNCIA DE CONTROLE DE ENDEMIAS': 'SUCEN',
 'SUTACO-SUP. TRAB. ARTESANAL COMUNIDADES - *EXTINTA PELA LEI Nº 15.828/2015 E DECRETO Nº 61.774/2015:': 'SUTACO'
 }

In [56]:
def conecta(df_irregular):
    df_irr = df_irregular.copy()
    df_irr['CARGO.1'] = df_irr.nome_orgao.map(dicionario_orgaos)
    df_irr.NOME = df_irr.NOME.str.upper()
    df_irr['CARGO OU FUNÇÃO EM COMISSÃO'] = (df_irr['CARGO OU FUNÇÃO EM COMISSÃO'].str.upper()
                                                    .str.normalize('NFD')
                                                    .str.encode('ascii',  'ignore')
                                                    .str.decode('utf-8'))
    return df_irr

In [57]:
df_irr_autarquias = conecta(df_comissionados_autarquias)
df_irr_fundacoes = conecta(df_comissionados_fundacoes)
df_irr_empresas = conecta(df_comissionados_empresas)

In [58]:
df_irr_autarquias.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3108 entries, 0 to 52066
Data columns (total 9 columns):
NOME                              3108 non-null object
CARGO PERMANENTE                  0 non-null object
CARGO OU FUNÇÃO EM COMISSÃO       3108 non-null object
UNIDADE DE TRABALHO               3108 non-null object
AFASTADO P/ OUTROS ÓRGÃOS         3108 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO    19 non-null object
nome_orgao                        3108 non-null object
nat_juridica                      3108 non-null object
CARGO.1                           3097 non-null object
dtypes: object(9)
memory usage: 242.8+ KB


In [59]:
df_irr_fundacoes.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 639 entries, 52077 to 71326
Data columns (total 9 columns):
NOME                              639 non-null object
CARGO PERMANENTE                  0 non-null object
CARGO OU FUNÇÃO EM COMISSÃO       639 non-null object
UNIDADE DE TRABALHO               638 non-null object
AFASTADO P/ OUTROS ÓRGÃOS         639 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO    29 non-null object
nome_orgao                        639 non-null object
nat_juridica                      639 non-null object
CARGO.1                           639 non-null object
dtypes: object(9)
memory usage: 49.9+ KB


In [60]:
df_irr_empresas.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2030 entries, 71332 to 112386
Data columns (total 9 columns):
NOME                              2030 non-null object
CARGO PERMANENTE                  0 non-null object
CARGO OU FUNÇÃO EM COMISSÃO       2030 non-null object
UNIDADE DE TRABALHO               2029 non-null object
AFASTADO P/ OUTROS ÓRGÃOS         2030 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO    273 non-null object
nome_orgao                        2030 non-null object
nat_juridica                      2030 non-null object
CARGO.1                           2030 non-null object
dtypes: object(9)
memory usage: 158.6+ KB


#### Tratamento de homônimos:

In [61]:
def trata_homonimos(df_irr):
    df_merge = pd.merge(df_irr, df_renda, how='inner',
                        left_on=['CARGO.1', 'NOME'],
                        right_on=['CARGO.1', 'NOME'])
    df_tmp = df_merge.groupby(['CARGO.1', 'NOME']).size().reset_index('NOME')
    homonimos = df_tmp.loc[df_tmp[0] > 1, 'NOME'].values
    df_irr_homonimos = df_irr[df_irr.NOME.isin(homonimos)]
    df_irr_regular = df_irr[~df_irr.NOME.isin(homonimos)]
    df_merge_regular = pd.merge(df_irr_regular, df_renda, how='inner',
                                left_on=['CARGO.1', 'NOME'],
                                right_on=['CARGO.1', 'NOME'])
    df_merge_homonimos = pd.merge(df_irr_homonimos, df_renda, how='inner',
                                  left_on=['CARGO.1', 'NOME', 'CARGO OU FUNÇÃO EM COMISSÃO'],
                                  right_on=['CARGO.1', 'NOME', 'CARGO'])
    df_todos = pd.concat([df_merge_homonimos, df_merge_regular])
    return df_todos

In [62]:
df_todos_autarquias = trata_homonimos(df_irr_autarquias)
df_todos_fundacoes = trata_homonimos(df_irr_fundacoes)
df_todos_empresas = trata_homonimos(df_irr_empresas)

In [63]:
df_todos_autarquias.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2053 entries, 0 to 2026
Data columns (total 17 columns):
NOME                                       2053 non-null object
CARGO PERMANENTE                           0 non-null object
CARGO OU FUNÇÃO EM COMISSÃO                2053 non-null object
UNIDADE DE TRABALHO                        2053 non-null object
AFASTADO P/ OUTROS ÓRGÃOS                  2053 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO             14 non-null object
nome_orgao                                 2053 non-null object
nat_juridica                               2053 non-null object
CARGO.1                                    2053 non-null object
CARGO                                      2053 non-null object
REMUNERAÇÃO DO MÊS                         2053 non-null float64
FÉRIAS E 13º SALÁRIO                       2053 non-null float64
PAGAMENTOS EVENTUAIS                       2053 non-null float64
LICENÇA PRÊMIO INDENIZADA                  2053 non-null float6

In [64]:
df_todos_fundacoes.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 478 entries, 0 to 476
Data columns (total 17 columns):
NOME                                       478 non-null object
CARGO PERMANENTE                           0 non-null object
CARGO OU FUNÇÃO EM COMISSÃO                478 non-null object
UNIDADE DE TRABALHO                        477 non-null object
AFASTADO P/ OUTROS ÓRGÃOS                  478 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO             24 non-null object
nome_orgao                                 478 non-null object
nat_juridica                               478 non-null object
CARGO.1                                    478 non-null object
CARGO                                      478 non-null object
REMUNERAÇÃO DO MÊS                         478 non-null float64
FÉRIAS E 13º SALÁRIO                       478 non-null float64
PAGAMENTOS EVENTUAIS                       478 non-null float64
LICENÇA PRÊMIO INDENIZADA                  478 non-null float64
ABONO PERMAN

In [65]:
df_todos_empresas.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1751 entries, 0 to 1735
Data columns (total 17 columns):
NOME                                       1751 non-null object
CARGO PERMANENTE                           0 non-null object
CARGO OU FUNÇÃO EM COMISSÃO                1751 non-null object
UNIDADE DE TRABALHO                        1750 non-null object
AFASTADO P/ OUTROS ÓRGÃOS                  1751 non-null object
ÓRGÃO - DESTINO DE AFASTAMENTO             219 non-null object
nome_orgao                                 1751 non-null object
nat_juridica                               1751 non-null object
CARGO.1                                    1751 non-null object
CARGO                                      1751 non-null object
REMUNERAÇÃO DO MÊS                         1751 non-null float64
FÉRIAS E 13º SALÁRIO                       1751 non-null float64
PAGAMENTOS EVENTUAIS                       1751 non-null float64
LICENÇA PRÊMIO INDENIZADA                  1751 non-null float

### Números gerais deduzidos a partir do cruzamento dos dois conjuntos de dados:

#### Número de 'comissionados puros' (inclusive homônimos):

In [66]:
len(df_irr_autarquias)

3108

In [67]:
len(df_irr_fundacoes)

639

In [68]:
len(df_irr_empresas)

2030

#### Número de 'comissionados puros' (inclusive homônimos) afastados [formalmente] para outros órgãos:

In [69]:
df_irr_autarquias['AFASTADO P/ OUTROS ÓRGÃOS'].value_counts().to_frame()

AFASTADO P/ OUTROS ÓRGÃOS
NÃO                       3089
SIM                         19

In [70]:
df_irr_fundacoes['AFASTADO P/ OUTROS ÓRGÃOS'].value_counts().to_frame()

AFASTADO P/ OUTROS ÓRGÃOS
NÃO                        610
SIM                         29

In [71]:
df_irr_empresas['AFASTADO P/ OUTROS ÓRGÃOS'].value_counts().to_frame()

AFASTADO P/ OUTROS ÓRGÃOS
NÃO                       1757
SIM                        273

#### Número de 'comissionados puros' (exclusive homônimos):

In [72]:
len(df_todos_autarquias)

2053

In [73]:
len(df_todos_fundacoes)

478

In [74]:
len(df_todos_empresas)

1751

#### Valor médio da remuneração mensal dos 'comissionados puros' (exclusive homônimos):

In [75]:
df_todos_autarquias['REMUNERAÇÃO DO MÊS'].mean()

4053.494383828544

In [76]:
df_todos_fundacoes['REMUNERAÇÃO DO MÊS'].mean()

8888.1264853556477

In [77]:
df_todos_empresas['REMUNERAÇÃO DO MÊS'].mean()

15800.306961736153

#### Valor médio da remuneração anual dos 'empregados em comissão' (inclusive homônimos):

In [78]:
df_todos_autarquias['REMUNERAÇÃO DO MÊS'].mean() * len(df_irr_autarquias) * (13 + 1/3) / 1e6

167.97680726585486

In [79]:
df_todos_fundacoes['REMUNERAÇÃO DO MÊS'].mean() * len(df_irr_fundacoes) * (13 + 1/3) / 1e6

75.726837655230113

In [80]:
df_todos_empresas['REMUNERAÇÃO DO MÊS'].mean() * len(df_irr_empresas) * (13 + 1/3) / 1e6

427.66164176432522

#### Cria arquivo tratado e consolidado com as informações contidas nos dois conjuntos de dados referentes a todos os 'comissionados puros' (exclusive homônimos):

In [81]:
df_todos_autarquias.to_csv('outputs/Quadro-Funcionarios-Remuneracao-Autarquias.csv') # Exclusive homônimos

In [82]:
df_todos_fundacoes.to_csv('outputs/Quadro-Funcionarios-Remuneracao-Fundacoes.csv') # Exclusive homônimos

In [83]:
df_todos_empresas.to_csv('outputs/Quadro-Funcionarios-Remuneracao-Empresas.csv') # Exclusive homônimos

In [84]:
df_todos_autarquias.head(2)

NOME CARGO PERMANENTE CARGO OU FUNÇÃO EM COMISSÃO  \
0  ADELIA MENEGARIO              NaN   ASSISTENTE ADMINISTRATIVO   
1    ADRIANO GRECCO              NaN          DIRETOR DE SERVICO   

                                UNIDADE DE TRABALHO AFASTADO P/ OUTROS ÓRGÃOS  \
0  ESCOLA TÉCNICA ESTADUAL JOSÉ MARTINIANO DA SILVA                       NÃO   
1         ESCOLA TÉCNICA ESTADUAL CÔNEGO JOSÉ BENTO                       NÃO   

  ÓRGÃO - DESTINO DE AFASTAMENTO  \
0                            NaN   
1                            NaN   

                                          nome_orgao nat_juridica  CARGO.1  \
0  CEETEPS - CENTRO DE EDUCAÇÃO TECNOLÓGICA PAULA...    Autarquia  CEETEPS   
1  CEETEPS - CENTRO DE EDUCAÇÃO TECNOLÓGICA PAULA...    Autarquia  CEETEPS   

                       CARGO  REMUNERAÇÃO DO MÊS  FÉRIAS E 13º SALÁRIO  \
0  ASSISTENTE ADMINISTRATIVO             2145.36               1430.24   
1         DIRETOR DE SERVICO             4191.87                  0.00   

   PAGAMENTOS EVENTUAIS  LICENÇA PRÊMIO INDENIZADA  \
0                   0.0                        0.0   
1                   0.0                        0.0   

   ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES  REDUTOR SALARIAL  \
0                                      0.0               0.0   
1                                      0.0               0.0   

   TOTAL LIQUÍDO (R$)  
0             3243.08  
1             3511.58

In [85]:
df_todos_fundacoes.head(2)

NOME CARGO PERMANENTE CARGO OU FUNÇÃO EM COMISSÃO  \
0     GUILHERME CONTI              NaN  ASSESSOR DE NOVAS MIDIAS I   
0  ALEXANDRE ROCCATTO              NaN  GERENTE DE AREA CIENTIFICA   

                 UNIDADE DE TRABALHO AFASTADO P/ OUTROS ÓRGÃOS  \
0  LICENCIAMENTO DE CONTEUDO E MARCA                       NÃO   
0                             FAPESP                       NÃO   

  ÓRGÃO - DESTINO DE AFASTAMENTO  \
0                            NaN   
0                            NaN   

                                          nome_orgao nat_juridica  \
0    FUNDAÇÃO PADRE ANCHIETA - RÁDIO E TV EDUCATIVAS     Fundação   
0  FAPESP - FUNDAÇÃO DE AMPARO À PESQUISA DO ESTA...     Fundação   

        CARGO.1                       CARGO  REMUNERAÇÃO DO MÊS  \
0  PE. ANCHIETA  ASSESSOR DE NOVAS MIDIAS I             1151.41   
0        FAPESP  GERENTE DE  REA CIENT FICA            20080.05   

   FÉRIAS E 13º SALÁRIO  PAGAMENTOS EVENTUAIS  LICENÇA PRÊMIO INDENIZADA  \
0                   0.0                   0.0                        0.0   
0                   0.0                   0.0                        0.0   

   ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES  REDUTOR SALARIAL  \
0                                      0.0               0.0   
0                                      0.0               0.0   

   TOTAL LIQUÍDO (R$)  
0             1025.29  
0             4946.24

In [86]:
df_todos_empresas.head(2)

NOME CARGO PERMANENTE   CARGO OU FUNÇÃO EM COMISSÃO  \
0  JORGE LUIZ AVILA DA SILVA              NaN            DIRETOR PRESIDENTE   
1  JORGE LUIZ AVILA DA SILVA              NaN  CONSELHEIRO DE ADMINISTRACAO   

                   UNIDADE DE TRABALHO AFASTADO P/ OUTROS ÓRGÃOS  \
0  COMPANHIA PAULISTA DE SECURITIZAÇÃO                       NÃO   
1  COMPANHIA PAULISTA DE SECURITIZAÇÃO                       NÃO   

  ÓRGÃO - DESTINO DE AFASTAMENTO                           nome_orgao  \
0                            NaN  COMPANHIA PAULISTA DE SECURITIZAÇÃO   
1                            NaN  COMPANHIA PAULISTA DE SECURITIZAÇÃO   

  nat_juridica CARGO.1                         CARGO  REMUNERAÇÃO DO MÊS  \
0      Empresa   CPSEC            DIRETOR PRESIDENTE             20590.0   
1      Empresa   CPSEC  CONSELHEIRO DE ADMINISTRACAO              6177.0   

   FÉRIAS E 13º SALÁRIO  PAGAMENTOS EVENTUAIS  LICENÇA PRÊMIO INDENIZADA  \
0                   0.0               30885.0                        0.0   
1                   0.0                   0.0                        0.0   

   ABONO PERMANÊNCIA & OUTRAS INDENIZAÇÕES  REDUTOR SALARIAL  \
0                                      0.0               0.0   
1                                      0.0               0.0   

   TOTAL LIQUÍDO (R$)  
0            14927.75  
1             5451.96

===== // =====